# Komputerowe wspomaganie tłumaczenia

# Zajęcia 11 - urównoleglanie

Na poprzednich zajęciach poznaliśmy techniki pozyskiwania tekstu z Internetu. Jeśli uda nam się w ten sposób pozyskać tekst w jednym języku oraz jego tłumaczenie na inny język, jesteśmy tylko o krok od uzyskania najbardziej przydatnego zasobu z punktu widzenia wspomagania tłumaczenia - pamięci tłumaczeń. Krokiem tym jest automatyczne urównoleglanie tekstu.

Automatyczne urównoleglanie tekstu składa się z dwóch kroków:
1. Podziału tekstu źródłowego oraz docelowego na zdania.
2. Dopasowaniu zdań źródłowych do docelowych.

Zdania, o których mowa w punkcie 1., powinniśmy rozumieć jako segmenty, tj. niekoniecznie kompletne zdania w sensie gramatycznym. Standardowym sposobem podziału tekstu na segmenty jest dzielenie po znaku nowej linii lub zaraz po kropce, o ile jest ona częścią sekwencji: ".[spacja][Wielka litera]"

### Ćwiczenie 1: Zaimplementuj podstawowy algorytm segmentacji tekstu. Użyj odpowiedniego wyrażenia regularnego, łapiącego wielkie litery w dowolnym języku, np. "Ż" (użyj klasy unikodowej). Zwróć listę segmentów.

In [23]:
import regex

def sentence_split(text):
    pattern = r'(?=\p{Lu})'
    segments = regex.split(pattern, text)
    
    segments = [segment for segment in segments if segment]
    return segments
    
text = "To JestŻywy.przykładŻebyŁadnie ZademonstrowaćSegmentację"
segments = sentence_split(text)
print(segments)

['To ', 'Jest', 'Żywy.przykład', 'Żeby', 'Ładnie ', 'Zademonstrować', 'Segmentację']


### Ćwiczenie 2: Uruchom powyższy algorytm na treści wybranej przez siebie strony internetowej (do ściągnięcia treści strony wykorzystaj kod z laboratoriów nr 7). Zidentyfikuj co najmniej dwa wyjątki od ogólnej reguły podziału na segmenty i ulepsz algorytm.

In [19]:
import requests
from bs4 import BeautifulSoup
import regex

url = 'https://amu.edu.pl/dla-mediow/komunikaty-prasowe/czy-dzikie-pszczoly-zagrazaja-pszczolom-miodnym'

def sentence_split(text):
    pattern = r'(?=\p{Lu})'
    segments = regex.split(pattern, text)
    segments = [segment.strip() for segment in segments if segment.strip()]
    return segments

page = requests.get(url)
soup = BeautifulSoup(page.content, 'html.parser')

article_content = soup.find('div', {'class': 'news__body'}).get_text()

segments = sentence_split(article_content)

for i, segment in enumerate(segments, 1):
    print(segment)

-
Dużo mówi się o tym, że to pszczoły miodne zagrażają dzikim pszczołom.
Tak przewrotnie postawione pytanie zmusza do zastanowienia, czy negatywna interakcja w drugą stronę jest możliwa - mówi dr
Jacek
Wendzonka.
I dodaje: -
Niestety, odpowiedź pozostaje ciągle taka sama.
Pszczoły, i dzikie i miodne, ewoluowały i współwystępowały razem przez miliony lat.
Oczywiście konkurowały one o zasoby pokarmowe, co doprowadzało do tworzenia rozmaitych strategii oraz specjalizacji i było jedną z sił napędowych ewolucji.
Pszczoła miodna (
Apis mellifera) jako gatunek społeczny, magazynujący zapasy i potrafiący wielokrotnie zimować w gnieździe jako rodzina, jest na szczycie drabiny ewolucyjnej.
Daje to szereg korzyści takich jak lepsza obrona przed wrogami, korzystanie z zapasów w okresach niedostatków, regulacja temperatury gniazda itp.
Niestety (dla dalszych rozważań), rodzina taka licząca nawet 30 – 50 tys. osobników, ma duże zapotrzebowanie energetyczne i wymaga odpowiedniej ilości pokarmu.
Przek

In [25]:
def sentence_split_enhanced(text):
    pattern = r'(?<!\w)(\p{Lu}.*?\.)(?=\s*\p{Lu}|\s*$)'
    segments = regex.findall(pattern, text, regex.DOTALL)
    segments = [segment.strip() for segment in segments if segment.strip()]
    return segments


article_content = soup.find('div', {'class': 'news__body'}).get_text()
segments = sentence_split_enhanced(article_content)

for i, segment in enumerate(segments, 1):
    print(segment)

Dużo mówi się o tym, że to pszczoły miodne zagrażają dzikim pszczołom.
Tak przewrotnie postawione pytanie zmusza do zastanowienia, czy negatywna interakcja w drugą stronę jest możliwa - mówi dr Jacek Wendzonka.
I dodaje: - Niestety, odpowiedź pozostaje ciągle taka sama.
Pszczoły, i dzikie i miodne, ewoluowały i współwystępowały razem przez miliony lat.
Oczywiście konkurowały one o zasoby pokarmowe, co doprowadzało do tworzenia rozmaitych strategii oraz specjalizacji i było jedną z sił napędowych ewolucji.
Pszczoła miodna (Apis mellifera) jako gatunek społeczny, magazynujący zapasy i potrafiący wielokrotnie zimować w gnieździe jako rodzina, jest na szczycie drabiny ewolucyjnej.
Daje to szereg korzyści takich jak lepsza obrona przed wrogami, korzystanie z zapasów w okresach niedostatków, regulacja temperatury gniazda itp.
Niestety (dla dalszych rozważań), rodzina taka licząca nawet 30 – 50 tys. osobników, ma duże zapotrzebowanie energetyczne i wymaga odpowiedniej ilości pokarmu.
Przekład

Po podziale tekstu na segmenty po stronie źródłowej oraz docelowej, możemy przystąpić do kroku drugiego - dopasowania segmentów. Głównym wyzwaniem tego kroku jest fakt, iż po stronie źródłowej może być inna liczba segmentów, niż po stronie docelowej. Takie rozbieżności są bardzo częste, a wynikają między innymi z:
* tłumaczenia jednego zdania źródłowego przy użyciu więcej niż jednego zdania
* tłumaczenia więcej niż jednego zdania źródłowego przy użyciu jednego zdania
* pominięcia zdania podczas tłumaczenia
* rozbieżności pomiędzy wersjami tekstu źródłowego i docelowego (np. tekst źródłowy mógł być modyfikowany po przetłumaczeniu i tłumaczenie nie zostało zaktualizowane)
* przetłumaczenia tekstu źródłowego tylko częściowo

Problemy te rozwiązwyane są na różne sposoby. Najpopularniejszym programem do przeprowadzania urównoleglania jest [Hunalign](https://github.com/danielvarga/hunalign). Wejściem do programu są dwa pliki, zawierające po jednym segmencie w linii. Wyjściem - plik urównoleglony w wewnętrznym formacie hunaligna.

### Ćwiczenie 3: Odnajdź dowolną stronę, która jest dostępna w wielu językach. Pobierz z tej strony tekst oryginalny (tylko ze strony głównej) oraz przetłumaczony na dowolny inny język. Przy użyciu Pythona przygotuj pliki dla Hunaligna i uruchom go.

In [8]:
import requests
from bs4 import BeautifulSoup

def fetch_and_save_text(url, filename):
    response = requests.get(url)
    response.raise_for_status()
    
    soup = BeautifulSoup(response.content, 'html.parser')
    text = soup.get_text()
    
    with open(filename, 'w', encoding='utf-8') as file:
        file.write(text)

def create_hunalign_file(file1, file2, output):
    with open(file1, 'r', encoding='utf-8') as f1, open(file2, 'r', encoding='utf-8') as f2:
        text1 = f1.read().strip().split('\n')
        text2 = f2.read().strip().split('\n')
        
    with open(output, 'w', encoding='utf-8') as out:
        for line1, line2 in zip(text1, text2):
            out.write(f"{line1}\n{line2}\n")

fetch_and_save_text('https://wolften.pl/pl/', 'wolften_pl.txt')
fetch_and_save_text('https://wolften.pl/cs/', 'wolften_cs.txt')

create_hunalign_file('wolften_pl.txt', 'wolften_cs.txt', 'hunalign_format')

Wyjściem z Hunaligna jest plik w specjalnym formacie Hunaligna. Problem jednak w tym, że niestety nie można go w prosty sposób zaimportować do jakiegokolwiek narzędzia typu CAT. Potrzebna jest konwersja do któregoś z bardziej popularnych formatów, np. XLIFF.

XLIFF jest formatem do przechowywania pamięci tłumaczeń, który opiera się na XML-u. Przykładowy plik XLIFF wygląda następująco:

### Ćwiczenie 4: Napisz konwerter formatu hunaligna na XLIFF.

In [10]:
import xml.etree.ElementTree as ET

def convert2xliff(hunalign_file, xliff_file):
    xliff = ET.Element('xliff', {
        'version': '1.2',
        'xmlns': 'urn:oasis:names:tc:xliff:document:1.2'
    })
    
    file_elem = ET.SubElement(xliff, 'file', {
        'source-language': 'pl',
        'target-language': 'cs',
        'datatype': 'plaintext',
        'original': hunalign_file
    })
    
    body = ET.SubElement(file_elem, 'body')
    
    with open(hunalign_file, 'r', encoding='utf-8') as f:
        lines = f.readlines()
        
        for i in range(0, len(lines), 2):
            source_text = lines[i].strip()
            target_text = lines[i + 1].strip()
            
            trans_unit = ET.SubElement(body, 'trans-unit', {
                'id': str(i // 2 + 1)
            })
            
            source = ET.SubElement(trans_unit, 'source')
            source.text = source_text
            
            target = ET.SubElement(trans_unit, 'target')
            target.text = target_text
    
    tree = ET.ElementTree(xliff)
    with open(xliff_file, 'wb') as f:
        tree.write(f, encoding='utf-8', xml_declaration=True)

convert2xliff('hunalign_format', 'xliff_format')